In [0]:
#!nohup python -u ./cifar_10_csawgan3.py > cmd.log   & tail -f cmd.log

In [0]:
#!pkill -f ./cifar_10_csawgan3.py


##setting up tensorboard

In [0]:
!pip uninstall tensorboard
!pip install --force-reinstall -q tf-nightly-2.0-preview
%load_ext tensorboard

In [0]:
!wget https://bin.equinox.io/c/4VmDzA7iaHb/ngrok-stable-linux-amd64.zip
!unzip ngrok-stable-linux-amd64.zip

In [0]:
LOG_DIR = "/content/drive/My Drive/Fall 2019/Deep Learning CSE 676/Projects/1/SA Gans/logs/"
get_ipython().system_raw(
    'tensorboard --logdir {} --host 0.0.0.0 --port 6086 &'
    .format(LOG_DIR)
)

In [0]:
get_ipython().system_raw('./ngrok http 6086 &')

In [0]:
! curl -s http://localhost:4040/api/tunnels | python3 -c \
    "import sys, json; print(json.load(sys.stdin)['tunnels'][0]['public_url'])"

https://d8244593.ngrok.io


In [0]:
%tensorboard --logdir="/content/drive/My Drive/Fall 2019/Deep Learning CSE 676/Projects/1/SA Gans/logs/"

##mounting google drive

In [0]:
from google.colab import drive
drive.mount('/content/drive/',force_remount=True)

Mounted at /content/drive/


##libraries and initializations

In [0]:
import torch 
import torchvision
from torch import nn, optim
from torch.autograd.variable import Variable
from torchvision import transforms, datasets
import os
from PIL import Image
import glob
import PIL
from PIL import ImageFont
from PIL import Image
from PIL import ImageDraw
import matplotlib.pyplot as plt
import random
from bokeh.io import curdoc, show, output_notebook
from bokeh.layouts import column
from bokeh.models import ColumnDataSource
from bokeh.plotting import figure
from functools import partial
from threading import Thread
from tornado import gen
import time
import pickle
from tqdm import tqdm
import torchvision.utils as vutils
from torch.utils.tensorboard import SummaryWriter

In [0]:
model='sagan'
adv_loss='wgan-gp'
imsize=64
g_num=5
z_dim=100
label_dim=10
g_conv_dim=64
d_conv_dim=64
lambda_gp=10
version='csawgan_trial3'

#training parameters
total_step=100000
d_iters=5
batch_size=64
num_workers=2
g_lr=0.0001
d_lr=0.0004
lr_decay=0.95
beta1=0
beta2=0.9

#pretrained
pretrained_model=None

#misc
train=True
parallel=False
dataset='cifar'
use_tensorboard=True

#paths
root_dir="/content/drive/My Drive/Fall 2019/Deep Learning CSE 676/Projects/1/SA Gans/"
#root_dir="./"
image_path=root_dir+"data"
log_path=root_dir+"logs"
model_save_path=root_dir+"models"
sample_path=root_dir+"samples"
attn_path=root_dir+"attn"
log_step=10
sample_step=100
model_save_step=1


Importing logger to keep a track of training progress 

##Dataloader

In [0]:
import torch
import torchvision.datasets as dsets
from torchvision import transforms


class Data_Loader():
    def __init__(self, train, dataset, image_path, image_size, batch_size, shuf=True):
        self.dataset = dataset
        self.path = image_path
        self.imsize = image_size
        self.batch = batch_size
        self.shuf = shuf
        self.train = train

    def transform(self, resize, totensor, normalize, centercrop):
        options = []
        if centercrop:
            options.append(transforms.CenterCrop(160))
        if resize:
            options.append(transforms.Resize((self.imsize,self.imsize)))
        if totensor:
            options.append(transforms.ToTensor())
        if normalize:
            options.append(transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)))
        transform = transforms.Compose(options)
        return transform

    def load_lsun(self, classes='church_outdoor_train'):
        transforms = self.transform(True, True, True, False)
        dataset = dsets.LSUN(self.path, classes=[classes], transform=transforms)
        return dataset

    def load_celeb(self):
        transforms = self.transform(True, True, True, True)
        dataset = dsets.ImageFolder(self.path+'/CelebA', transform=transforms)
        return dataset


    def loader(self):
        if self.dataset == 'lsun':
            dataset = self.load_lsun()
        elif self.dataset == 'celeb':
            dataset = self.load_celeb()

        loader = torch.utils.data.DataLoader(dataset=self.dataset,
                                              batch_size=self.batch,
                                              shuffle=self.shuf,
                                              num_workers=2,
                                              drop_last=True)
        return loader
      
    def loader(self):
      transform = transforms.Compose(
          [transforms.Resize((self.imsize,self.imsize)),
           transforms.ToTensor(),
           transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

      dataset_full = torchvision.datasets.CIFAR10(root='./data', train=True,
                                              download=True, transform=transform)
      train_split=0.8
      train_size=int(train_split*len(dataset_full))
      val_size=len(dataset_full)-train_size
      trainset, valset=torch.utils.data.random_split(dataset_full,[train_size,val_size])
      trainloader = torch.utils.data.DataLoader(trainset, batch_size=batch_size,
                                                shuffle=True, num_workers=2)
      
      return trainloader
    def len(self):
      return len(self.loader())

##Spectral


In [0]:
import torch
from torch.optim.optimizer import Optimizer, required

from torch.autograd import Variable
import torch.nn.functional as F
from torch import nn
from torch import Tensor
from torch.nn import Parameter

def l2normalize(v, eps=1e-12):
    return v / (v.norm() + eps)


class SpectralNorm(nn.Module):
    def __init__(self, module, name='weight', power_iterations=1):
        super(SpectralNorm, self).__init__()
        self.module = module
        self.name = name
        self.power_iterations = power_iterations
        if not self._made_params():
            self._make_params()

    def _update_u_v(self):
        u = getattr(self.module, self.name + "_u")
        v = getattr(self.module, self.name + "_v")
        w = getattr(self.module, self.name + "_bar")

        height = w.data.shape[0]
        for _ in range(self.power_iterations):
            v.data = l2normalize(torch.mv(torch.t(w.view(height,-1).data), u.data))
            u.data = l2normalize(torch.mv(w.view(height,-1).data, v.data))

        # sigma = torch.dot(u.data, torch.mv(w.view(height,-1).data, v.data))
        sigma = u.dot(w.view(height, -1).mv(v))
        setattr(self.module, self.name, w / sigma.expand_as(w))

    def _made_params(self):
        try:
            u = getattr(self.module, self.name + "_u")
            v = getattr(self.module, self.name + "_v")
            w = getattr(self.module, self.name + "_bar")
            return True
        except AttributeError:
            return False


    def _make_params(self):
        w = getattr(self.module, self.name)

        height = w.data.shape[0]
        width = w.view(height, -1).data.shape[1]

        u = Parameter(w.data.new(height).normal_(0, 1), requires_grad=False)
        v = Parameter(w.data.new(width).normal_(0, 1), requires_grad=False)
        u.data = l2normalize(u.data)
        v.data = l2normalize(v.data)
        w_bar = Parameter(w.data)

        del self.module._parameters[self.name]

        self.module.register_parameter(self.name + "_u", u)
        self.module.register_parameter(self.name + "_v", v)
        self.module.register_parameter(self.name + "_bar", w_bar)


    def forward(self, *args):
        self._update_u_v()
        return self.module.forward(*args)

##models

In [0]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable
import numpy as np

class Self_Attn(nn.Module):
    #Self attention Layer
    def __init__(self,in_dim,activation):
        super(Self_Attn,self).__init__()
        self.chanel_in = in_dim
        self.activation = activation
        
        self.query_conv = nn.Conv2d(in_channels = in_dim , out_channels = in_dim//8 , kernel_size= 1)
        self.key_conv = nn.Conv2d(in_channels = in_dim , out_channels = in_dim//8 , kernel_size= 1)
        self.value_conv = nn.Conv2d(in_channels = in_dim , out_channels = in_dim , kernel_size= 1)
        self.gamma = nn.Parameter(torch.zeros(1))

        self.softmax  = nn.Softmax(dim=-1) #
    def forward(self,x):

        m_batchsize,C,width ,height = x.size()
        proj_query  = self.query_conv(x).view(m_batchsize,-1,width*height).permute(0,2,1) # B X CX(N)
        proj_key =  self.key_conv(x).view(m_batchsize,-1,width*height) # B X C x (*W*H)
        energy =  torch.bmm(proj_query,proj_key) # transpose check
        attention = self.softmax(energy) # BX (N) X (N) 
        proj_value = self.value_conv(x).view(m_batchsize,-1,width*height) # B X C X N

        out = torch.bmm(proj_value,attention.permute(0,2,1) )
        out = out.view(m_batchsize,C,width,height)
        
        out = self.gamma*out + x
        return out,attention

class Generator(nn.Module):
    """Generator."""

    def __init__(self, batch_size, image_size=64, z_dim=100, label_dim=10,conv_dim=64):
        super(Generator, self).__init__()
        self.imsize = image_size
        layer1 = []
        layer2 = []
        layer3 = []
        last = []

        repeat_num = int(np.log2(self.imsize)) - 3
        mult = 2 ** repeat_num # 8
        layer1.append(SpectralNorm(nn.ConvTranspose2d(z_dim, (conv_dim * mult), 4)))
        layer1.append(nn.BatchNorm2d(conv_dim * mult))
        layer1.append(nn.ReLU())
        

        curr_dim = conv_dim * mult

        layer2.append(SpectralNorm(nn.ConvTranspose2d(curr_dim, int(curr_dim / 2), 4, 2, 1)))
        layer2.append(nn.BatchNorm2d(int(curr_dim / 2)))
        layer2.append(nn.ReLU())

        curr_dim = int(curr_dim / 2)

        layer3.append(SpectralNorm(nn.ConvTranspose2d(curr_dim, int(curr_dim / 2), 4, 2, 1)))
        layer3.append(nn.BatchNorm2d(int(curr_dim / 2)))
        layer3.append(nn.ReLU())
        
        if self.imsize == 64:
            layer4 = []
            curr_dim = int(curr_dim / 2)
            layer4.append(SpectralNorm(nn.ConvTranspose2d(curr_dim, int(curr_dim / 2), 4, 2, 1)))
            layer4.append(nn.BatchNorm2d(int(curr_dim / 2)))
            layer4.append(nn.ReLU())
            self.l4 = nn.Sequential(*layer4)
            curr_dim = int(curr_dim / 2)

        self.l1 = nn.Sequential(*layer1)
        self.l2 = nn.Sequential(*layer2)
        self.l3 = nn.Sequential(*layer3)

        last.append(nn.ConvTranspose2d(curr_dim, 3, 4, 2, 1))
        last.append(nn.Tanh())
        self.last = nn.Sequential(*last)

        self.attn1 = Self_Attn( 128, 'relu')
        self.attn2 = Self_Attn( 64,  'relu')

    def forward(self, z,label=None):
        z=torch.cat([z,label],1)
        z = z.view(z.size(0), z.size(1), 1, 1)
        out=self.l1(z)
        out=self.l2(out)
        out=self.l3(out)
        out,p1 = self.attn1(out)
        out=self.l4(out)
        out,p2 = self.attn2(out)
        out=self.last(out)

        return out, p1, p2


class Discriminator(nn.Module):
    """Discriminator, Auxiliary Classifier."""

    def __init__(self, batch_size=64, image_size=64,label_dim=10, conv_dim=64):
        super(Discriminator, self).__init__()
        self.imsize = image_size
        layer1 = []
        layer2 = []
        layer3 = []
        last = []
        hidden=[]

        layer1.append(SpectralNorm(nn.Conv2d(3, (conv_dim), 4, 2, 1)))
        layer1.append(nn.LeakyReLU(0.1))


        curr_dim = conv_dim

        layer2.append(SpectralNorm(nn.Conv2d(curr_dim, curr_dim * 2, 4, 2, 1)))
        layer2.append(nn.LeakyReLU(0.1))
        curr_dim = curr_dim * 2

        layer3.append(SpectralNorm(nn.Conv2d(curr_dim, curr_dim * 2, 4, 2, 1)))
        layer3.append(nn.LeakyReLU(0.1))
        curr_dim = curr_dim * 2

        if self.imsize == 64:
            layer4 = []
            layer4.append(SpectralNorm(nn.Conv2d(curr_dim, curr_dim * 2, 4, 2, 1)))
            layer4.append(nn.LeakyReLU(0.1))
            self.l4 = nn.Sequential(*layer4)
            curr_dim = curr_dim*2
        self.l1 = nn.Sequential(*layer1)
        self.l2 = nn.Sequential(*layer2)
        self.l3 = nn.Sequential(*layer3)

        last.append(nn.Conv2d(curr_dim, curr_dim*2, 4))
        curr_dim = curr_dim * 2
        hidden.append(nn.Linear(1034,1))
        
        self.last = nn.Sequential(*last)
        self.hidden=nn.Sequential(*hidden)
        
        self.attn1 = Self_Attn(256, 'relu')
        self.attn2 = Self_Attn(512, 'relu')

    def forward(self, x,label):
        out = self.l1(x)
        out = self.l2(out)
        out = self.l3(out)
        out,p1 = self.attn1(out)
        out=self.l4(out)
        out,p2 = self.attn2(out)
        out=self.last(out)
        #out=out.view(-1)
        
        out = out.reshape(out.size(0), -1)
        out=torch.cat([out,label],1) # Should it be axis 1 or 0
        #check if 
        out=self.hidden(out)

        return out.squeeze(), p1, p2

##utils

In [0]:
import os
import torch
from torch.autograd import Variable


def make_folder(path, version):
        if not os.path.exists(os.path.join(path, version)):
            os.makedirs(os.path.join(path, version))


def tensor2var(x, grad=False):
    if torch.cuda.is_available():
        x = x.cuda()
    return Variable(x, requires_grad=grad)

def var2tensor(x):
    return x.data.cpu()

def var2numpy(x):
    return x.data.cpu().numpy()

def denorm(x):
    out = (x + 1) / 2
    return out.clamp_(0, 1)
  
def encode(label):
  final_res=[]
  labels={'airplane':0,										
            'automobile':1,										
            'bird':2,										
            'cat':3,										
            'deer':4,										
            'dog':5,										
            'frog':6,										
            'horse':7,										
            'ship':8,										
            'truck':9}
  for l in label:
    res=[0]*10
    res[l]=1
    final_res.append(res)
  return torch.Tensor(final_res)
#logger=Logger(log_path)
def log_scalar(numerical_info,step):
  
  for tag, value in numerical_info.items():
      logger.scalar_summary(tag, value, step+1)

  #for tag, images in image_info.items():
   #   logger.image_summary(tag, images, step+1)

import math
import os
import warnings
import numpy as np
from scipy import linalg
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.autograd as autograd
import torch.optim as optim
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from tqdm import tqdm_notebook as tqdm

class FID():
    def __init__(self, cache_dir, device='cpu', transform_input=True):
        #cuda:0
        os.environ["TORCH_HOME"] = "./Cache"
        self.device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
        self.transform_input = transform_input
        self.InceptionV3 = models.inception_v3(pretrained=True, transform_input=False, aux_logits=False).to(device=self.device)
        self.InceptionV3.eval()
    
    def build_maps(self, x):
        # Resize to Fit InceptionV3
        if list(x.shape[-2:]) != [299,299]:
            with warnings.catch_warnings():
                warnings.simplefilter("ignore")
                x = F.interpolate(x, size=[299,299], mode='bilinear')
        # Transform Input to InceptionV3 Standards
        if self.transform_input:
            x_ch0 = torch.unsqueeze(x[:, 0], 1) * (0.229 / 0.5) + (0.485 - 0.5) / 0.5
            x_ch1 = torch.unsqueeze(x[:, 1], 1) * (0.224 / 0.5) + (0.456 - 0.5) / 0.5
            x_ch2 = torch.unsqueeze(x[:, 2], 1) * (0.225 / 0.5) + (0.406 - 0.5) / 0.5
            x = torch.cat((x_ch0, x_ch1, x_ch2), 1)
        # Run Through Partial InceptionV3 Model
        with torch.no_grad():
            # N x 3 x 299 x 299
            x = self.InceptionV3.Conv2d_1a_3x3(x)
            # N x 32 x 149 x 149
            x = self.InceptionV3.Conv2d_2a_3x3(x)
            # N x 32 x 147 x 147
            x = self.InceptionV3.Conv2d_2b_3x3(x)
            # N x 64 x 147 x 147
            x = F.max_pool2d(x, kernel_size=3, stride=2)
            # N x 64 x 73 x 73
            x = self.InceptionV3.Conv2d_3b_1x1(x)
            # N x 80 x 73 x 73
            x = self.InceptionV3.Conv2d_4a_3x3(x)
            # N x 192 x 71 x 71
            x = F.max_pool2d(x, kernel_size=3, stride=2)
            # N x 192 x 35 x 35
            x = self.InceptionV3.Mixed_5b(x)
            # N x 256 x 35 x 35
            x = self.InceptionV3.Mixed_5c(x)
            # N x 288 x 35 x 35
            x = self.InceptionV3.Mixed_5d(x)
            # N x 288 x 35 x 35
            x = self.InceptionV3.Mixed_6a(x)
            # N x 768 x 17 x 17
            x = self.InceptionV3.Mixed_6b(x)
            # N x 768 x 17 x 17
            x = self.InceptionV3.Mixed_6c(x)
            # N x 768 x 17 x 17
            x = self.InceptionV3.Mixed_6d(x)
            # N x 768 x 17 x 17
            x = self.InceptionV3.Mixed_6e(x)
            # N x 768 x 17 x 17
            x = self.InceptionV3.Mixed_7a(x)
            # N x 1280 x 8 x 8
            x = self.InceptionV3.Mixed_7b(x)
            # N x 2048 x 8 x 8
            x = self.InceptionV3.Mixed_7c(x)
            # N x 2048 x 8 x 8
            # Adaptive average pooling
            x = F.adaptive_avg_pool2d(x, (1, 1))
            # N x 2048 x 1 x 1
            return x
    
    def compute_fid(self, real_images, generated_images, batch_size=64):
        # Ensure Set Sizes are the Same
        assert(real_images.shape[0] == generated_images.shape[0])
        # Build Random Sampling Orders
        real_images = real_images[np.random.permutation(real_images.shape[0])]
        generated_images = generated_images[np.random.permutation(generated_images.shape[0])]
        # Lists of Maps per Batch
        real_maps = []
        generated_maps = []
        # Build Maps
        for s in tqdm(range(math.ceil(real_images.shape[0]/batch_size)), desc='Evaluation', leave=False):
            sidx = np.arange(batch_size*s, min(batch_size*(s+1), real_images.shape[0]))
            real_maps.append(self.build_maps(real_images[sidx].to(device=self.device)).detach().to(device='cpu'))
            generated_maps.append(self.build_maps(generated_images[sidx].to(device=self.device)).detach().to(device='cpu'))
        # Concatenate Maps
        real_maps = np.squeeze(torch.cat(real_maps).numpy())
        generated_maps = np.squeeze(torch.cat(generated_maps).numpy())
        # Calculate FID
        # Activation Statistics
        mu_g = np.mean(generated_maps, axis=0)
        mu_x = np.mean(real_maps, axis=0)
        sigma_g = np.cov(generated_maps, rowvar=False)
        sigma_x = np.cov(real_maps, rowvar=False)
        # Sum of Squared Differences
        ssd = np.sum((mu_g - mu_x)**2)
        # Square Root of Product of Covariances
        covmean = linalg.sqrtm(sigma_g.dot(sigma_x), disp=False)[0]
        if np.iscomplexobj(covmean):
            covmean = covmean.real
        # Final FID Computation
        return ssd + np.trace(sigma_g + sigma_x - 2*covmean)


##train

In [0]:
import os
import time
import torch
import datetime

import torch.nn as nn
from torch.autograd import Variable
from torchvision.utils import save_image

class Trainer(object):
    def __init__(self, data_loader):

        # Data loader
        self.data_loader = data_loader

        # exact model and loss
        self.model = model
        self.adv_loss = adv_loss

        # Model hyper-parameters
        self.imsize = imsize
        self.g_num = g_num
        self.z_dim = z_dim
        self.g_conv_dim = g_conv_dim
        self.d_conv_dim = d_conv_dim
        self.parallel = parallel

        self.lambda_gp = lambda_gp
        self.total_step = total_step
        self.d_iters = d_iters
        self.batch_size = batch_size
        self.num_workers = num_workers
        self.g_lr = g_lr
        self.d_lr = d_lr
        self.lr_decay = lr_decay
        self.beta1 = beta1
        self.beta2 = beta2
        self.pretrained_model = pretrained_model

        self.dataset = dataset
        self.use_tensorboard = use_tensorboard
        self.image_path = image_path
        self.log_path = log_path
        self.model_save_path = model_save_path
        self.sample_path = sample_path
        self.log_step = log_step
        self.sample_step = sample_step
        self.model_save_step = model_save_step
        self.version = version
        device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
        self.fid_model=FID("./log_path",device) # as a var log path not a string changed

        # Path
        #self.log_path = os.path.join(log_path, self.version)
        self.sample_path = os.path.join(sample_path, self.version)
        self.model_save_path = os.path.join(model_save_path, self.version)

        self.build_model()

        if self.use_tensorboard:
            self.build_tensorboard()

        # Start with trained model
        if self.pretrained_model:
            self.load_pretrained_model()
          
        #tensor board writer
        self.writer = SummaryWriter(log_path)



    def train(self):

        device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
        # Data iterator
        data_iter = iter(self.data_loader)
        step_per_epoch = len(self.data_loader)
        model_save_step = int(self.model_save_step * step_per_epoch)

        # Fixed input for debugging
        fixed_z = tensor2var(torch.randn(self.batch_size,90 )) #self.z_dim

        # Start with trained model
        if self.pretrained_model:
            start = self.pretrained_model + 1
        else:
            start = 0
        
        # Start time
        start_time = time.time()
        for step in range(start, self.total_step):

            # ================== Train D ================== #
            self.D.train()
            self.G.train()

            try:
                real_images, labels = next(data_iter)
            except:
                data_iter = iter(self.data_loader)
                real_images, labels = next(data_iter)

            # Compute loss with real images
            real_images = tensor2var(real_images)
            labels=tensor2var(encode(labels))
            d_out_real,dr1,dr2 = self.D(real_images,labels) #labels not added in generator, generator still not sorted.
            
            d_loss_real = - torch.mean(d_out_real)
            

            z = tensor2var(torch.randn(real_images.size(0), 90))
            fake_images,gf1,gf2 = self.G(z,labels)
            d_out_fake,df1,df2 = self.D(fake_images,labels)

            
            d_loss_fake = d_out_fake.mean()
           


            # Backward + Optimize
            d_loss = d_loss_real + d_loss_fake
            self.reset_grad()
            d_loss.backward()
            self.d_optimizer.step()


            if self.adv_loss == 'wgan-gp':
                # gradient penalty
                alpha = torch.rand(real_images.size(0), 1, 1, 1).to(device).expand_as(real_images)
                interpolated = Variable(alpha * real_images.data + (1 - alpha) * fake_images.data, requires_grad=True)
                out,_,_ = self.D(interpolated,labels)

                grad = torch.autograd.grad(outputs=out,
                                           inputs=interpolated,
                                           grad_outputs=torch.ones(out.size()).to(device),
                                           retain_graph=True,
                                           create_graph=True,
                                           only_inputs=True)[0]

                grad = grad.view(grad.size(0), -1)
                grad_l2norm = torch.sqrt(torch.sum(grad ** 2, dim=1))
                d_loss_gp = torch.mean((grad_l2norm - 1) ** 2)

                # Backward + Optimize
                d_loss = self.lambda_gp * d_loss_gp

                self.reset_grad()
                d_loss.backward()
                self.d_optimizer.step()

            # ================== Train G and gumbel ================== #
            # Create random noise
            z = tensor2var(torch.randn(real_images.size(0), 90)) #self.z_dim
            fake_images,_,_ = self.G(z,labels)

            # Compute loss with fake images
            g_out_fake,_,_ = self.D(fake_images,labels)  # batch x n
            if self.adv_loss == 'wgan-gp':
                g_loss_fake = - g_out_fake.mean()
            elif self.adv_loss == 'hinge':
                g_loss_fake = - g_out_fake.mean()

            self.reset_grad()
            g_loss_fake.backward()
            self.g_optimizer.step()
            

            # Print out log info
            if (step + 1) % self.log_step == 0:
                elapsed = time.time() - start_time
                elapsed = str(datetime.timedelta(seconds=elapsed))
                
                log_info={'G_loss':g_loss_fake.item(),'D_loss':g_loss_fake.item()}
                self.writer.add_scalar('G_loss',g_loss_fake.item(),step)
                self.writer.add_scalar('D_loss',d_loss.item(),step)                  
                print("Elapsed [{}], G_step [{}/{}], D_step[{}/{}],  "
                      " G_Loss: {:.4f}, D Loss: {:.4f}".
                      format(elapsed, step + 1, self.total_step, (step + 1),
                             self.total_step ,
                             g_loss_fake.item(), d_loss.item()))

            # Sample images
            if (step + 1) % self.sample_step == 0:
                fake_images,_,_= self.G(fixed_z,labels)
                fid_score=self.fid_model.compute_fid(real_images, fake_images)
                self.writer.add_scalar('FID_score',fid_score.item(),step)
                save_image(denorm(fake_images.data),
                           os.path.join(self.sample_path, '{}_fake.png'.format(step + 1)))
                print("Elapsed [{}], G_step [{}/{}], D_step[{}/{}],  "
                      " FID score: {:.4f}".
                      format(elapsed, step + 1, self.total_step, (step + 1),
                             self.total_step ,
                             fid_score.item()))

            if (step+1) % model_save_step==0:
                torch.save(self.G.state_dict(),
                           os.path.join(self.model_save_path, '{}_G.pth'.format(step + 1)))
                torch.save(self.D.state_dict(),
                           os.path.join(self.model_save_path, '{}_D.pth'.format(step + 1)))
        self.writer.close()

    def build_model(self):
        device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
        self.G = Generator(self.batch_size,self.imsize, self.z_dim, self.g_conv_dim).to(device)
        self.D = Discriminator(self.batch_size,self.imsize, self.d_conv_dim).to(device)
        if self.parallel:
            self.G = nn.DataParallel(self.G)
            self.D = nn.DataParallel(self.D)

        # Loss and optimizer
        # self.g_optimizer = torch.optim.Adam(self.G.parameters(), self.g_lr, [self.beta1, self.beta2])
        self.g_optimizer = torch.optim.Adam(filter(lambda p: p.requires_grad, self.G.parameters()), self.g_lr, [self.beta1, self.beta2])
        self.d_optimizer = torch.optim.Adam(filter(lambda p: p.requires_grad, self.D.parameters()), self.d_lr, [self.beta1, self.beta2])

        self.c_loss = torch.nn.CrossEntropyLoss()


    def build_tensorboard(self):
        return
        #from logger import Logger
        #self.logger = Logger(self.log_path)

    def load_pretrained_model(self):
        self.G.load_state_dict(torch.load(os.path.join(
            self.model_save_path, '{}_G.pth'.format(self.pretrained_model))))
        self.D.load_state_dict(torch.load(os.path.join(
            self.model_save_path, '{}_D.pth'.format(self.pretrained_model))))
        print('loaded trained models (step: {})..!'.format(self.pretrained_model))

    def reset_grad(self):
        self.d_optimizer.zero_grad()
        self.g_optimizer.zero_grad()

    def save_sample(self, data_iter):
        real_images, _ = next(data_iter)
        save_image(denorm(real_images), os.path.join(self.sample_path, 'real.png'))

In [0]:
load_pre

##utils

In [0]:

import itertools, imageio, torch
import matplotlib.pyplot as plt
import numpy as np
from torchvision import datasets
#from scipy.misc import imresize
#import PIL
#import pilutil


def ones_target(size):
  #returning tensor variable containing ones, with shape =size
  data=Variable(torch.ones(size,1))
  return data

def zeros_target(size):
  data=Variable(torch.zeros(size,1))
  return data

def images_to_vectors(images):
  return images.view(images.size(0),3072) #parameters: (size to flatten(28 here, row size), no. of images to be flattened)

def vectors_to_images(vectors):
  return vectors.view(vectors.size(0),3,32,32) # to convert each row of vectors to 28x28 pixels images 
# parameteres: (initial flattened dim, no. of sub vectors to be converted to 2d, 2d dimensions of output )

def show_result(G, x_, num_epoch, show = False, save = False, path = 'result.png'):
    # G.eval()
    y_ = G(x_)
    y_=y_[:4]
    y_ = y_.cpu()

    size_figure_grid = 3
    fig, ax = plt.subplots(x_.size()[0], size_figure_grid, figsize=(5, 5))
    for i, j in itertools.product(range(x_.size()[0]), range(size_figure_grid)):
        ax[i, j].get_xaxis().set_visible(False)
        ax[i, j].get_yaxis().set_visible(False)

    for i in range(y_.size()[0],2):

        ax[i, 0].cla()
        ax[i, 0].imshow((y_[i].numpy().transpose(1, 2, 0) + 1) / 2)
        ax[i, 1].cla()
        ax[i, 1].imshow((y_[i+1].numpy().transpose(1, 2, 0) + 1) / 2)

    label = 'Epoch {0}'.format(num_epoch)
    fig.text(0.5, 0.04, label, ha='center')

    if save:
        plt.savefig(path)

    if show:
        plt.show()
    else:
        plt.close()

def show_train_hist(hist, show = False, save = False, path = 'Train_hist.png'):
    x = range(len(hist['D_losses']))

    y1 = hist['D_losses']
    y2 = hist['G_losses']

    plt.plot(x, y1, label='D_loss')
    plt.plot(x, y2, label='G_loss')

    plt.xlabel('Iter')
    plt.ylabel('Loss')

    plt.legend(loc=4)
    plt.grid(True)
    plt.tight_layout()

    if save:
        plt.savefig(path)

    if show:
        plt.show()
    else:
        plt.close()

def generate_animation(root, model, opt):
    images = []
    for e in range(opt.train_epoch):
        img_name = root + 'Fixed_results/' + model + str(e + 1) + '.png'
        images.append(imageio.imread(img_name))
    imageio.mimsave(root + model + 'generate_animation.gif', images, fps=5)

def data_load(path, subfolder, transform, batch_size, shuffle=True):
    dset = datasets.ImageFolder(path, transform)
    ind = dset.class_to_idx[subfolder]

    n = 0
    for i in range(dset.__len__()):
        if ind != dset.imgs[n][1]:
            del dset.imgs[n]
            n -= 1

        n += 1

    return torch.utils.data.DataLoader(dset, batch_size=batch_size, shuffle=shuffle)

def imgs_resize(imgs, resize_scale = 286):
    outputs = torch.FloatTensor(imgs.size()[0], imgs.size()[1], resize_scale, resize_scale)
    for i in range(imgs.size()[0]):
        img = imresize(imgs[i].numpy(), [resize_scale, resize_scale])
        outputs[i] = torch.FloatTensor((img.transpose(2, 0, 1).astype(np.float32).reshape(-1, imgs.size()[1], resize_scale, resize_scale) - 127.5) / 127.5)

    return outputs

def random_crop(imgs1, imgs2, crop_size = 256):
    outputs1 = torch.FloatTensor(imgs1.size()[0], imgs1.size()[1], crop_size, crop_size)
    outputs2 = torch.FloatTensor(imgs2.size()[0], imgs2.size()[1], crop_size, crop_size)
    for i in range(imgs1.size()[0]):
        img1 = imgs1[i]
        img2 = imgs2[i]
        rand1 = np.random.randint(0, imgs1.size()[2] - crop_size)
        rand2 = np.random.randint(0, imgs2.size()[2] - crop_size)
        outputs1[i] = img1[:, rand1: crop_size + rand1, rand2: crop_size + rand2]
        outputs2[i] = img2[:, rand1: crop_size + rand1, rand2: crop_size + rand2]

    return outputs1, outputs2

def random_fliplr(imgs1, imgs2):
    outputs1 = torch.FloatTensor(imgs1.size())
    outputs2 = torch.FloatTensor(imgs2.size())
    for i in range(imgs1.size()[0]):
        if torch.rand(1)[0] < 0.5:
            img1 = torch.FloatTensor(
                (np.fliplr(imgs1[i].numpy().transpose(1, 2, 0)).transpose(2, 0, 1).reshape(-1, imgs1.size()[1], imgs1.size()[2], imgs1.size()[3]) + 1) / 2)
            outputs1[i] = (img1 - 0.5) / 0.5
            img2 = torch.FloatTensor(
                (np.fliplr(imgs2[i].numpy().transpose(1, 2, 0)).transpose(2, 0, 1).reshape(-1, imgs2.size()[1], imgs2.size()[2], imgs2.size()[3]) + 1) / 2)
            outputs2[i] = (img2 - 0.5) / 0.5
        else:
            outputs1[i] = imgs1[i]
            outputs2[i] = imgs2[i]

    return outputs1, outputs2

def imshow(img):
    img = img / 2 + 0.5     # unnormalize
    npimg = img.numpy()
    plt.imshow(np.transpose(npimg, (1, 2, 0)))
    plt.show()
    
def noise(size):
  n=Variable(torch.randn(size,200))
  return n
 
def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)

##main

In [0]:

from torch.backends import cudnn

cudnn.benchmark=True
# Data loader
data_loader = Data_Loader(train, dataset, image_path, imsize,
                        batch_size, shuf=train)


# Create directories if not exist
make_folder(model_save_path, version)
make_folder(sample_path,version)
make_folder(log_path,version)
make_folder(attn_path,version)


if train:
    if model=='sagan':
        trainer = Trainer(data_loader.loader())
    elif model == 'qgan':
        trainer = qgan_trainer(data_loader.loader())
    trainer.train()
else:
    tester = Tester(data_loader.loader())
    tester.test()

Files already downloaded and verified
Elapsed [0:00:05.925931], G_step [10/100000], D_step[10/100000],   G_Loss: 0.0785, D Loss: 31.0177
Elapsed [0:00:11.769588], G_step [20/100000], D_step[20/100000],   G_Loss: 20.4856, D Loss: 13.4836
Elapsed [0:00:17.630695], G_step [30/100000], D_step[30/100000],   G_Loss: 8.2839, D Loss: 12.6940
Elapsed [0:00:23.487745], G_step [40/100000], D_step[40/100000],   G_Loss: 13.7454, D Loss: 10.5995
Elapsed [0:00:29.351472], G_step [50/100000], D_step[50/100000],   G_Loss: 4.7852, D Loss: 4.5721
Elapsed [0:00:35.231070], G_step [60/100000], D_step[60/100000],   G_Loss: 2.0055, D Loss: 2.0269
Elapsed [0:00:41.110198], G_step [70/100000], D_step[70/100000],   G_Loss: -4.3858, D Loss: 0.1744
Elapsed [0:00:47.003251], G_step [80/100000], D_step[80/100000],   G_Loss: 4.6400, D Loss: 0.2529
Elapsed [0:00:52.898308], G_step [90/100000], D_step[90/100000],   G_Loss: -8.4190, D Loss: 5.0601


Evaluation:   0%|          | 0/1 [00:00<?, ?it/s]

Elapsed [0:00:58.772503], G_step [100/100000], D_step[100/100000],   G_Loss: 1.3166, D Loss: 0.2260


Elapsed [0:00:58.772503], G_step [100/100000], D_step[100/100000],   FID score: 394.6883
Elapsed [0:01:23.058341], G_step [110/100000], D_step[110/100000],   G_Loss: -6.6033, D Loss: 2.4126
Elapsed [0:01:28.942368], G_step [120/100000], D_step[120/100000],   G_Loss: -14.0910, D Loss: 4.7331
Elapsed [0:01:34.827965], G_step [130/100000], D_step[130/100000],   G_Loss: -2.7796, D Loss: 3.8602
Elapsed [0:01:40.713717], G_step [140/100000], D_step[140/100000],   G_Loss: 4.7072, D Loss: 1.6678
Elapsed [0:01:46.612216], G_step [150/100000], D_step[150/100000],   G_Loss: -8.6472, D Loss: 2.2360
Elapsed [0:01:52.517179], G_step [160/100000], D_step[160/100000],   G_Loss: -14.7401, D Loss: 3.7366
Elapsed [0:01:58.409708], G_step [170/100000], D_step[170/100000],   G_Loss: -22.2490, D Loss: 1.1633
Elapsed [0:02:04.316966], G_step [180/100000], D_step[180/100000],   G_Loss: -22.3574, D Loss: 2.5932
Elapsed [0:02:10.223104], G_step [190/100000], D_step[190/100000],   G_Loss: -18.5713, D Loss: 4.550

Evaluation:   0%|          | 0/1 [00:00<?, ?it/s]

...

Elapsed [7:28:15.849218], G_step [34600/100000], D_step[34600/100000],   FID score: 173.6640
Elapsed [7:28:40.120654], G_step [34610/100000], D_step[34610/100000],   G_Loss: -701.5980, D Loss: 0.0299
Elapsed [7:28:46.071717], G_step [34620/100000], D_step[34620/100000],   G_Loss: -696.5912, D Loss: 0.0578
Elapsed [7:28:52.078617], G_step [34630/100000], D_step[34630/100000],   G_Loss: -656.4254, D Loss: 0.0733
Elapsed [7:28:58.041495], G_step [34640/100000], D_step[34640/100000],   G_Loss: -672.5302, D Loss: 0.2539
Elapsed [7:29:04.008402], G_step [34650/100000], D_step[34650/100000],   G_Loss: -654.1705, D Loss: 0.0997
Elapsed [7:29:09.975390], G_step [34660/100000], D_step[34660/100000],   G_Loss: -648.7628, D Loss: 0.1347
Elapsed [7:29:15.976762], G_step [34670/100000], D_step[34670/100000],   G_Loss: -633.4888, D Loss: 0.0635
Elapsed [7:29:21.926255], G_step [34680/100000], D_step[34680/100000],   G_Loss: -646.4421, D Loss: 0.0465
Elapsed [7:29:27.938607], G_step [34690/100000], D_

Evaluation:   0%|          | 0/1 [00:00<?, ?it/s]

Elapsed [7:29:33.897305], G_step [34700/100000], D_step[34700/100000],   G_Loss: -669.9421, D Loss: 0.0425


Elapsed [7:29:33.897305], G_step [34700/100000], D_step[34700/100000],   FID score: 169.8704


KeyboardInterrupt: ignored